# Hyper parameter search for TD3+BC

In [4]:
!pip install d3rlpy

In [5]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import math
import subprocess
import os
import d3rlpy
# plt.style.use('matplotlibrc')

# from Python.data_sampler import *

## Building an MDPDataset

We first read in a large batch of samples from the file. As `d3rlpy` wants it in the form (observations, actions, rewards, terminal flags), we go ahead and do that. Here's a helper function to get a dataset from a list of chunks of your choosing.

In [6]:
import numpy as np
import torch
import random
import pandas
from Python.data_sampler import *

In [7]:
def get_dataset(chunks : list, batch_size=30000, 
                path="collected_data/rl_det_small.txt") -> d3rlpy.dataset.MDPDataset :
    random.seed(0)
    samples = DataSampler(path_to_data=path)
    samples.setting("coarse")
    states = []
    actions = []
    rewards = []
    next_states = []
    for chunk in chunks:
        samples.use_chunk(chunk)
        samples.read_chunk()
        [statesChunk, actionsChunk, rewardsChunk, nextStatesChunk] = samples.get_batch(batch_size)
        states.append(statesChunk)
        actions.append(actionsChunk)
        rewards.append(rewardsChunk)
        next_states.append(nextStatesChunk)
    states = torch.cat(states)
    actions = torch.cat(actions)
    rewards = torch.cat(rewards)
    next_states = torch.cat(next_states)
    terminals = np.zeros(len(states))
    terminals[::1111] = 1 #episode length 100, change if necessary
    print(states.shape)
    dataset = d3rlpy.dataset.MDPDataset(states.numpy(), 
                                        actions.numpy(), 
                                        rewards.numpy(), terminals)
    return dataset, states.numpy(), actions.numpy(), rewards.numpy()

We can build the dataset from there, just like this, and split into train and test sets.

In [8]:
dataset, states, actions, rewards = get_dataset([i for  i in range(100)], path="../collected_data/rl_purestochastic.txt")

start
[ 0.00000000e+00  7.95731469e+08 -4.75891077e-02 -3.69999953e-02
  2.00999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.50429671e-01 -4.92727243e-01 -5.31666025e-03]
Read chunk # 1 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  3.25610892e-01 -3.35999953e-02
 -2.42000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -3.08749986e-01  6.00000000e-01 -6.00000000e-01]
Read chunk # 2 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.90489108e-01 -5.87999953e-02
 -1.01000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.76979602e-02 -6.00000000e-01  6.00000000e-01]
Read chunk # 3 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  4.48010892e-01  4.64000047e-02
 -1.04000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -4.83151637e-01  6.00000000e-01 -6.00000000e-01]
Read chunk # 4 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.08389108e-01  3.32000047e-02
 -2.02000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -4.25137655

[ 0.00000000e+00  7.95731469e+08  3.09110892e-01  5.60000047e-02
 -7.30001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -3.36295348e-01  6.00000000e-01 -6.00000000e-01]
Read chunk # 45 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  8.95108923e-02  3.40000047e-02
  1.95999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01  3.06837024e-02 -6.00000000e-01]
Read chunk # 46 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.56189108e-01  5.80000047e-02
  1.50999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.51481072e-01 -2.88867043e-01  6.00000000e-01]
Read chunk # 47 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  1.14110892e-01  5.68000047e-02
  7.99998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.54213589e-03  3.91473614e-01 -9.17637410e-02]
Read chunk # 48 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.60389108e-01  1.12000047e-02
  1.94999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  2.68637874e-

[ 0.00000000e+00  7.95731469e+08 -7.15891077e-02 -7.99999531e-03
  2.33999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  5.79765872e-01 -3.17402568e-01  6.00000000e-01]
Read chunk # 97 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.09789108e-01 -4.57999953e-02
 -2.20000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -2.84885686e-01 -2.78683294e-01  6.00000000e-01]
Read chunk # 98 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.58389108e-01  5.40000469e-03
 -2.15000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01 -4.93350106e-01  6.00000000e-01]
Read chunk # 99 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.20589108e-01  1.38000047e-02
 -2.59000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01 -6.00000000e-01  6.00000000e-01]
Read chunk # 100 out of 4999
torch.Size([111000, 6])


In [9]:
print("The behavior policy value statistics are:")
dataset.compute_stats()['return']

The behavior policy value statistics are:


{'mean': -136.20181,
 'std': 106.013954,
 'min': -410.7058,
 'max': 0.0,
 'histogram': (array([ 4,  1,  4,  2,  1,  0,  3,  2,  5,  2,  0,  2,  6,  5,  8, 13, 12,
         28,  1,  1]),
  array([-410.7058  , -390.17053 , -369.63522 , -349.09995 , -328.56464 ,
         -308.02936 , -287.49408 , -266.95877 , -246.4235  , -225.8882  ,
         -205.3529  , -184.81761 , -164.28232 , -143.74704 , -123.21175 ,
         -102.67645 ,  -82.14116 ,  -61.605873,  -41.07058 ,  -20.53529 ,
            0.      ], dtype=float32))}

In [10]:
from sklearn.model_selection import train_test_split
train_episodes, test_episodes = train_test_split(dataset, test_size=0.2)

## Setting up an Algorithm

In [11]:
from d3rlpy.algos import CQL, TD3PlusBC
from d3rlpy.models.encoders import VectorEncoderFactory

from d3rlpy.preprocessing import MinMaxActionScaler
import random
action_scaler = MinMaxActionScaler(minimum=-0.6, maximum=0.6)

from d3rlpy.metrics.scorer import td_error_scorer
from d3rlpy.metrics.scorer import average_value_estimation_scorer
from d3rlpy.metrics.scorer import initial_state_value_estimation_scorer

from d3rlpy.ope import FQE
# metrics to evaluate with
from d3rlpy.metrics.scorer import soft_opc_scorer
import pickle as pkl
from statistics import harmonic_mean as hm

## Perform a random search on hyper params. 

As good fqe on both stochastic and deterministic data is needed for good performance during the evaluation step in the simulator, we take the harmonic mean of both fqes to understand the performance on each dataset. The harmonic mean is large only when each number whose mean is being taken is large. Therefore, a large harmonic mean corresponds to large numbers whose mean is being taken.


In [12]:

# The number of times we would wanna do a random search for hyper-params. In 
# every random search, we randomly pick a new set of hyper-params.
num_search_iterations = 40
largest_fqe = -np.inf

for i in range(num_search_iterations):

    random.seed()

    actor_lr_this_iter = random.uniform(1e-5, 1e-2)
    critic_lr_this_iter = random.uniform(1e-5, 1e-2)
    temp_lr_this_iter = random.uniform(1e-5, 1e-4)
    n_steps_this_iter = random.choice([1, 3, 5, 7])

    actor_encoder = VectorEncoderFactory(hidden_units=[12, 24, 36, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)
    critic_encoder = VectorEncoderFactory(hidden_units=[12, 24, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)

    print("search iteration: ", i)
    print("using hyper params: ", [actor_lr_this_iter, critic_lr_this_iter, 
                                   temp_lr_this_iter, n_steps_this_iter])

    model = TD3PlusBC(q_func_factory='qr', #qr -> quantile regression q function, but you don't have to use this
                reward_scaler='standard',
#                 actor_encoder_factory = actor_encoder,
#                 critic_encoder_factory = critic_encoder,
                action_scaler=action_scaler,
                actor_learning_rate=actor_lr_this_iter, 
                critic_learning_rate=critic_lr_this_iter,
                n_steps=n_steps_this_iter, 
                use_gpu=True) #change it to true if you have one
    model.build_with_dataset(dataset)

    model.fit(train_episodes,
        eval_episodes=test_episodes,
        n_epochs=50, 
        tensorboard_dir='runs',
        scorers={
            'td_error': td_error_scorer,
            'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+100 for i  in range(20)], 
                                                                    path="../collected_data/rl_stochpid.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_stoch = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+200 for i in range(40)], 
                                                                    path="../collected_data/rl_purestochastic.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_det = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    if(hm([history_stoch[-1][1]["ave_value"] + 50, 
           history_det[-1][1]["ave_value"] + 50]) \
                                                          > largest_fqe):
        largest_fqe = hm([history_stoch[-1][1]["ave_value"] + 50, 
                         history_det[-1][1]["ave_value"] + 50])

        # Save the hyper-params
        hyperparams = [actor_lr_this_iter, critic_lr_this_iter, 
                       temp_lr_this_iter, n_steps_this_iter]

        with open("hyperparams_td3bc.pkl", "wb") as f:
            print("most optimal hyper params for td3+bc at this point: ", hyperparams)
            pkl.dump(hyperparams, f)

        # Save model and policy
        model.save_model("model_hyperparams_td3bc.pt")
        model.save_policy("policy_hyperparams_td3bc.pt")


search iteration:  0
using hyper params:  [0.0037935400354651636, 0.004050689617073905, 2.8020594664729005e-05, 7]
2022-04-20 15:25.50 [debug    ] RoundIterator is selected.
2022-04-20 15:25.50 [info     ] Directory is created at d3rlpy_logs/TD3PlusBC_20220420152550
2022-04-20 15:25.50 [debug    ] Fitting scaler...              scaler=standard
2022-04-20 15:25.50 [debug    ] Fitting action scaler...       action_scaler=min_max
2022-04-20 15:25.50 [debug    ] Fitting reward scaler...       reward_scaler=standard
2022-04-20 15:25.50 [warning  ] Skip building models since they're already built.
2022-04-20 15:25.50 [info     ] Parameters are saved to d3rlpy_logs/TD3PlusBC_20220420152550/params.json params={'action_scaler': {'type': 'min_max', 'params': {'minimum': array(-0.6), 'maximum': array(0.6)}}, 'actor_encoder_factory': {'type': 'default', 'params': {'activation': 'relu', 'use_batch_norm': False, 'dropout_rate': None}}, 'actor_learning_rate': 0.0037935400354651636, 'actor_optim_facto

Epoch 1/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-20 15:25.53 [info     ] TD3PlusBC_20220420152550: epoch=1 step=342 epoch=1 metrics={'time_sample_batch': 0.0002855327394273546, 'time_algorithm_update': 0.008629117095679567, 'critic_loss': 12.349660272138161, 'actor_loss': 2.666534257911102, 'time_step': 0.008966750568813749, 'td_error': 1.0774244199433352, 'init_value': -11.435041427612305, 'ave_value': -7.221264671509129} step=342
2022-04-20 15:25.53 [info     ] Model parameters are saved to d3rlpy_logs/TD3PlusBC_20220420152550/model_342.pt


Epoch 2/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-20 15:25.57 [info     ] TD3PlusBC_20220420152550: epoch=2 step=684 epoch=2 metrics={'time_sample_batch': 0.00029121923167803136, 'time_algorithm_update': 0.008063409063551161, 'critic_loss': 6.0128394013259845, 'actor_loss': 2.5793802933386196, 'time_step': 0.008403367466396756, 'td_error': 1.3118598827780752, 'init_value': -16.009353637695312, 'ave_value': -10.190275628280297} step=684
2022-04-20 15:25.57 [info     ] Model parameters are saved to d3rlpy_logs/TD3PlusBC_20220420152550/model_684.pt


...

2022-04-20 18:51.59 [info     ] FQE_20220420185049: epoch=49 step=16856 epoch=49 metrics={'time_sample_batch': 0.00016964937365332314, 'time_algorithm_update': 0.0035656711389852125, 'loss': 0.7224260081515409, 'time_step': 0.0038099406763564708, 'init_value': -24.327266693115234, 'ave_value': -26.87019950480427, 'soft_opc': nan} step=16856


2022-04-20 18:51.59 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220420185049/model_16856.pt


Epoch 50/50:   0%|          | 0/344 [00:00<?, ?it/s]

2022-04-20 18:52.00 [info     ] FQE_20220420185049: epoch=50 step=17200 epoch=50 metrics={'time_sample_batch': 0.00017110414283220157, 'time_algorithm_update': 0.003558977398761483, 'loss': 0.7392019134361384, 'time_step': 0.0038058494412621787, 'init_value': -24.275476455688477, 'ave_value': -26.837951458895343, 'soft_opc': nan} step=17200


2022-04-20 18:52.00 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220420185049/model_17200.pt


## Reading hyper params from file

In [13]:
with open("hyperparams_td3bc.pkl", "rb") as f:
    data = pkl.load(f)

print(data)

[0.0012009373312255548, 0.007673227118548031, 7.942796560357695e-05, 1]
